# Ax Service API with RayTune on PyTorch CNN

Ax integrates easily with different scheduling frameworks and distributed training frameworks. In this example, Ax-driven optimization is executed in a distributed fashion using [RayTune](https://ray.readthedocs.io/en/latest/tune.html). 

RayTune is a scalable framework for hyperparameter tuning that provides many state-of-the-art hyperparameter tuning algorithms and seamlessly scales from laptop to distributed cluster with fault tolerance. RayTune leverages [Ray](https://ray.readthedocs.io/)'s Actor API to provide asynchronous parallel and distributed execution.

Ray 'Actors' are a simple and clean abstraction for replicating your Python classes across multiple workers and nodes. Each hyperparameter evaluation is asynchronously executed on a separate Ray actor and reports intermediate training progress back to RayTune. Upon reporting, RayTune then uses this information to performs actions such as early termination, re-prioritization, or checkpointing.

In [1]:
import logging

from ray import tune
from ray.tune import track
from ray.tune.suggest.ax import AxSearch

logger = logging.getLogger(tune.__name__)
logger.setLevel(
    level=logging.CRITICAL
)  # Reduce the number of Ray warnings that are not relevant here.

In [2]:
import numpy as np
import torch
from ax.plot.contour import plot_contour
from ax.plot.trace import optimization_trace_single_method
from ax.service.ax_client import AxClient
from ax.utils.notebook.plotting import init_notebook_plotting, render
from ax.utils.tutorials.cnn_utils import CNN, evaluate, load_mnist, train

init_notebook_plotting()

[INFO 12-08 18:53:21] ax.utils.notebook.plotting: Injecting Plotly library into cell. Do not overwrite or delete cell.


## 1. Initialize client
We specify `enforce_sequential_optimization` as False, because Ray runs many trials in parallel. With the sequential optimization enforcement, `AxClient` would expect the first few trials to be completed with data before generating more trials.

When high parallelism is not required, it is best to enforce sequential optimization, as it allows for achieving optimal results in fewer (but sequential) trials. In cases where parallelism is important, such as with distributed training using Ray, we choose to forego minimizing resource utilization and run more trials in parallel.

In [3]:
ax = AxClient(enforce_sequential_optimization=False)

[INFO 12-08 18:53:21] ax.service.ax_client: Starting optimization with verbose logging. To disable logging, set the `verbose_logging` argument to `False`. Note that float values in the logs are rounded to 2 decimal points.


## 2. Set up experiment
Here we set up the search space and specify the objective; refer to the Ax API tutorials for more detail.

In [4]:
ax.create_experiment(
    name="mnist_experiment",
    parameters=[
        {"name": "lr", "type": "range", "bounds": [1e-6, 0.4], "log_scale": True},
        {"name": "momentum", "type": "range", "bounds": [0.0, 1.0]},
    ],
    objective_name="mean_accuracy",
)

[INFO 12-08 18:53:21] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter lr. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.


[INFO 12-08 18:53:21] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter momentum. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.


[INFO 12-08 18:53:21] ax.modelbridge.dispatch_utils: Using Bayesian Optimization generation strategy: GenerationStrategy(name='Sobol+GPEI', steps=[Sobol for 5 trials, GPEI for subsequent trials]). Iterations after 5 will take longer to generate due to  model-fitting.


## 3. Define how to evaluate trials
Since we use the Ax Service API here, we evaluate the parameterizations that Ax suggests, using RayTune. The evaluation function follows its usual pattern, taking in a parameterization and outputting an objective value. For detail on evaluation functions, see [Trial Evaluation](https://ax.dev/docs/runner.html). 

In [5]:
def train_evaluate(parameterization):
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    train_loader, valid_loader, test_loader = load_mnist(data_path="~/.data")
    net = train(
        net=CNN(),
        train_loader=train_loader,
        parameters=parameterization,
        dtype=torch.float,
        device=device,
    )
    track.log(
        mean_accuracy=evaluate(
            net=net,
            data_loader=valid_loader,
            dtype=torch.float,
            device=device,
        )
    )

## 4. Run optimization
Execute the Ax optimization and trial evaluation in RayTune using [AxSearch algorithm](https://ray.readthedocs.io/en/latest/tune-searchalg.html#ax-search):

In [6]:
tune.run(
    train_evaluate,
    num_samples=30,
    search_alg=AxSearch(ax_client=ax, max_concurrent=3),
    verbose=0,  # Set this level to 1 to see status updates and to 2 to also see trial results.
    # To use GPU, specify: resources_per_trial={"gpu": 1}.
)

2020-12-08 18:53:22,401	INFO services.py:1092 -- View the Ray dashboard at http://127.0.0.1:8265


[INFO 12-08 18:53:24] ax.service.ax_client: Generated new trial 0 with parameters {'lr': 0.0, 'momentum': 0.21}.


[INFO 12-08 18:53:24] ax.service.ax_client: Generated new trial 1 with parameters {'lr': 0.0, 'momentum': 0.93}.


[INFO 12-08 18:53:24] ax.service.ax_client: Generated new trial 2 with parameters {'lr': 0.01, 'momentum': 0.75}.


2020-12-08 18:53:24,594	WARNING worker.py:1091 -- Failed to unpickle actor class 'ImplicitFunc' for actor ID 7bbd902801000000. Traceback:
Traceback (most recent call last):
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/function_manager.py", line 493, in _load_actor_class_from_gcs
    actor_class = pickle.loads(pickled_class)
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/__init__.py", line 2, in <module>
    from ray.tune.tune import run_experiments, run
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/tune.py", line 7, in <module>
    from ray.tune.analysis import ExperimentAnalysis
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/__init__.py", line 1, in <module>
    from ray.tune.analysis.experiment_analysis import ExperimentAnalysis, Analysis
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/experiment_analy

...

2020-12-08 18:53:37,608	WARNING worker.py:1091 -- Failed to unpickle actor class 'ImplicitFunc' for actor ID 296a970401000000. Traceback:
Traceback (most recent call last):
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/function_manager.py", line 493, in _load_actor_class_from_gcs
    actor_class = pickle.loads(pickled_class)
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/__init__.py", line 2, in <module>
    from ray.tune.tune import run_experiments, run
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/tune.py", line 7, in <module>
    from ray.tune.analysis import ExperimentAnalysis
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/__init__.py", line 1, in <module>
    from ray.tune.analysis.experiment_analysis import ExperimentAnalysis, Analysis
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/experiment_analy

(pid=4880) 2020-12-08 18:53:37,601	ERROR function_manager.py:495 -- Failed to load actor class ImplicitFunc.
(pid=4880) Traceback (most recent call last):
(pid=4880)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/function_manager.py", line 493, in _load_actor_class_from_gcs
(pid=4880)     actor_class = pickle.loads(pickled_class)
(pid=4880)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/__init__.py", line 2, in <module>
(pid=4880)     from ray.tune.tune import run_experiments, run
(pid=4880)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/tune.py", line 7, in <module>
(pid=4880)     from ray.tune.analysis import ExperimentAnalysis
(pid=4880)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/__init__.py", line 1, in <module>
(pid=4880)     from ray.tune.analysis.experiment_analysis import ExperimentAnalysis, Analysis
(pid=4880)   File "/home/travis/virt

2020-12-08 18:53:37,901	WARNING worker.py:1091 -- Failed to unpickle actor class 'ImplicitFunc' for actor ID f3b32ee701000000. Traceback:
Traceback (most recent call last):
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/function_manager.py", line 493, in _load_actor_class_from_gcs
    actor_class = pickle.loads(pickled_class)
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/__init__.py", line 2, in <module>
    from ray.tune.tune import run_experiments, run
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/tune.py", line 7, in <module>
    from ray.tune.analysis import ExperimentAnalysis
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/__init__.py", line 1, in <module>
    from ray.tune.analysis.experiment_analysis import ExperimentAnalysis, Analysis
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/experiment_analy

(pid=4898) 2020-12-08 18:53:37,894	ERROR function_manager.py:495 -- Failed to load actor class ImplicitFunc.
(pid=4898) Traceback (most recent call last):
(pid=4898)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/function_manager.py", line 493, in _load_actor_class_from_gcs
(pid=4898)     actor_class = pickle.loads(pickled_class)
(pid=4898)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/__init__.py", line 2, in <module>
(pid=4898)     from ray.tune.tune import run_experiments, run
(pid=4898)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/tune.py", line 7, in <module>
(pid=4898)     from ray.tune.analysis import ExperimentAnalysis
(pid=4898)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/__init__.py", line 1, in <module>
(pid=4898)     from ray.tune.analysis.experiment_analysis import ExperimentAnalysis, Analysis
(pid=4898)   File "/home/travis/virt

TuneError: ('Trials did not complete', [train_evaluate_a62ae542, train_evaluate_a62ae543, train_evaluate_a62ae544, train_evaluate_a62ae545, train_evaluate_a62ae546, train_evaluate_a62ae547, train_evaluate_a62ae548, train_evaluate_a7501014, train_evaluate_a7501015, train_evaluate_a7501016, train_evaluate_a7501017, train_evaluate_a88ec902, train_evaluate_a88ec903, train_evaluate_a88ec904, train_evaluate_a88ec905, train_evaluate_a88ec906, train_evaluate_a9c379ee, train_evaluate_a9c379ef, train_evaluate_a9c379f0, train_evaluate_a9c379f1, train_evaluate_aaf1e22e, train_evaluate_aaf1e22f, train_evaluate_aaf1e230, train_evaluate_aaf1e231, train_evaluate_ac475294, train_evaluate_ac475295, train_evaluate_ac475296, train_evaluate_ac475297, train_evaluate_ad761cc2, train_evaluate_ad761cc3])

## 5. Retrieve the optimization results

In [7]:
best_parameters, values = ax.get_best_parameters()
best_parameters

{'lr': 0.001200477766990381, 'momentum': 0.6754525434808601}

In [8]:
means, covariances = values
means

{'mean_accuracy': 0.9713334434324482}

## 6. Plot the response surface and optimization trace

In [9]:
render(
    plot_contour(
        model=ax.generation_strategy.model,
        param_x="lr",
        param_y="momentum",
        metric_name="mean_accuracy",
    )
)

/Users/deriksson/opt/anaconda3/lib/python3.8/site-packages/ax/modelbridge/torch.py:311: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).



In [10]:
# `plot_single_method` expects a 2-d array of means, because it expects to average means from multiple
# optimization runs, so we wrap out best objectives array in another array.
best_objectives = np.array(
    [[trial.objective_mean * 100 for trial in ax.experiment.trials.values()]]
)
best_objective_plot = optimization_trace_single_method(
    y=np.maximum.accumulate(best_objectives, axis=1),
    title="Model performance vs. # of iterations",
    ylabel="Accuracy",
)
render(best_objective_plot)